<img src="https://avatars.githubusercontent.com/u/74911464?s=200&v=4"
     alt="OpenEO Platform logo"
     style="float: left; margin-right: 10px;" />
# openEO Platform - Analysis Ready Data

# Get started with openEO Platform: Basics
** Review article "The openEO API–Harmonising the Use of Earth Observation Cloud Services Using Virtual Data Cube Functionalities"**
https://www.researchgate.net/publication/350109855_The_openEO_API-Harmonising_the_Use_of_Earth_Observation_Cloud_Services_Using_Virtual_Data_Cube_Functionalities

#### Review:
https://hub.openeo.org/

####  Review: 
https://editor.openeo.cloud/  

#### Review:
https://openeo.org/documentation/1.0/datacubes.html

**Connect to openEO Platform and print list of available collections**

In [ ]:
!pip install rasterio

In [ ]:
#copy required libraries
!cp /home/jovyan/mystorage/EENSAT/software/lib* /home/jovyan/.local/lib/

In [ ]:
#load all required libraries
from ctypes import *
lib1 = cdll.LoadLibrary(r'/home/jovyan/.local/lib/libGLdispatch.so.0.0.0')
lib1 = cdll.LoadLibrary(r'/home/jovyan/.local/lib/libGLX.so.0.0.0')
lib1 = cdll.LoadLibrary(r'/home/jovyan/.local/lib/libGL.so.1.7.0')

lib1 = cdll.LoadLibrary('/opt/conda/lib/libpython3.11.so.1.0')
lib1 = cdll.LoadLibrary('/opt/conda/envs/openeo/lib/libQt5Gui.so.5')
lib1 = cdll.LoadLibrary('/opt/conda/envs/openeo/lib/libQt5Sql.so.5')
lib1 = cdll.LoadLibrary('/opt/conda/envs/openeo/lib/libQt5Concurrent.so.5')

In [ ]:
pip install /home/jovyan/mystorage/EENSAT/software/ilwis-1.0.20230718-cp311-cp311-linux_x86_64.whl

In [ ]:
import matplotlib.pyplot as plt
import rasterio
import openeo
from zipfile import ZipFile
from datetime import date
import ilwis
import os
import numpy as np

In [ ]:
#suppress warnings
import warnings
warnings.filterwarnings('ignore')
warnings.simplefilter('ignore')

In [ ]:
openeo.__version__

In [ ]:
ilwis.version()

### Example GEE

In [ ]:
connection = openeo.connect("https://earthengine.openeo.org")

In [ ]:
#connection.authenticate_basic("username", "password")

print("Authenticate with Basic authentication")
connection.authenticate_basic("group1", "test123")

In [ ]:
print(connection.list_collection_ids())

**Print 1st collection from the list**

Note number, starts from 0

In [ ]:
print(connection.list_collections()[0])

In [ ]:
print(connection.list_collections()[0:3])

**Get detailed information about a collection**

In [ ]:
#print(connection.describe_collection("NASA/GPM_L3/IMERG_MONTHLY_V06")) #text listing NASA/GPM_L3/IMERG_MONTHLY_V06
connection.describe_collection("NASA/GPM_L3/IMERG_MONTHLY_V06")#web listing

In [ ]:
connection.describe_collection('ACA/reef_habitat/v1_0')

In [ ]:
connection.describe_collection("COPERNICUS/Landcover/100m/Proba-V-C3/Global")

**List processes that can be applied on the (EO) data**

#### Retrieve single image / map
Sample code
see: https://docs.openeo.cloud/getting-started/python/#batch-job-execution

In [ ]:
# Load data cube from GEE collection.
cube = connection.load_collection(
    "COPERNICUS/Landcover/100m/Proba-V-C3/Global",
    spatial_extent={"west": 28.780, "south": -2.929, "east": 30.984, "north": -0.9595},
    temporal_extent=["2015-01-01", "2019-12-31"],
    bands=["discrete_classification"],
)

In [ ]:
cube.download('data/lc.GTIFF-ZIP')

In [ ]:
z = ZipFile('data/lc.GTIFF-ZIP')
for file in z.filelist:
    outfile = file.filename.replace('download.','')
    foutp = open('data/' + outfile,'wb')
    foutp.write(z.read(file.filename))

In [ ]:
with rasterio.open('data/' + outfile) as ds:
    data = ds.read(1)

In [ ]:
fig, (ax1, ax2) = plt.subplots(ncols=2, figsize=(14, 10))
im = ax1.imshow(data, cmap = 'jet', vmin=0, vmax=150)
plt.colorbar(im, ax=ax1, orientation="horizontal")
ax1.set_title("Land Cover Map")
ax2.hist(data.flat, bins=32)
ax2.set_title("PCP Histogram")
ax2.set_xlabel("Land Cover Value")
ax2.set_ylabel("frequency");

#### Multi temporal import
Currently GEE in OpenEO does not facilitate multiband tif file creation and download. Now a loop is used to import single time steps to lateron create a multitemporal dataset

In [ ]:
# Load data cube from GEE collection.

def download(date_start, date_end, date_start_fn):
    cube = connection.load_collection(
        "NASA/GPM_L3/IMERG_MONTHLY_V06",
        spatial_extent={"west": 28.780, "south": -2.929, "east": 30.984, "north": -0.9595},
        temporal_extent=[date_start, date_end],
        bands=["precipitation"],
    )
    cube.download('data/pcp_imerg_'+date_start_fn+'.GTIFF-ZIP')
    z = ZipFile('data/pcp_imerg_'+date_start_fn+'.GTIFF-ZIP')
    for file in z.filelist:
        outfile = file.filename.replace('download.','')
        outfile = outfile[:-4] + '_' + date_start_fn + '.tif'
        foutp = open('data/' + outfile,'wb')
        foutp.write(z.read(file.filename))

In [ ]:
year = 2020
for month in range(1,13):
    date_start = date(year, month, 1)
    if month < 12:
        date_end = date(year, month + 1, 1)
    else:
        date_end = date(year+1, 1, 1)
    date_start_fn = date_start.strftime('%Y%m%d')
    print('Downloading', date_start_fn)
    download(date_start,date_end,date_start_fn)    

In [ ]:
# check data set created, here April 2020
with rasterio.open('data/precipitation_20200401.tif') as ds:
    data = ds.read(1)
data = data * 24 * 31 #initial data in mm/hr

In [ ]:
fig, (ax1, ax2) = plt.subplots(ncols=2, figsize=(14, 10))
im = ax1.imshow(data, cmap = 'turbo')
plt.colorbar(im, ax=ax1, orientation="horizontal")
ax1.set_title("PCP Map")
ax2.hist(data.flat, bins=32)
ax2.set_title("PCP Histogram")
ax2.set_xlabel("PCP value")
ax2.set_ylabel("frequency");

In [ ]:
work_dir = os.getcwd() + '/data'#use python function os.getcwd() to show the current folder used and add sub-folder
ilwis.setWorkingCatalog(work_dir) #set the working directory for ILWISPy
print(work_dir)

In [ ]:
ds = rasterio.open('data/precipitation_20200901.tif')
data = ds.read(1)
#data = data * 24 * 31 #initial data in mm/hr
size = np.shape(data)

In [ ]:
lonmin = ds.transform[2]
latmax = ds.transform[5]
lonmax = lonmin + size[1] * ds.transform[0]
latmin = latmax + size[0] * ds.transform[4]
envelope = str(lonmin) + ' ' + str(latmax) + ' ' + str(lonmax) + ' ' + str(latmin)

In [ ]:
ds.close()

In [ ]:
#grf = ilwis.GeoReference("epsg:4326", ilwis.Envelope(envelope) , ilwis.Size(size[1],size[0]))
grf = ilwis.GeoReference('code=georef:type=corners,csy=epsg:4326,envelope=' + envelope + ',gridsize=' + str(size[1]) + ' ' + str(size[0]) + ',cornerofcorners=yes,name=pcp')
dfNum = ilwis.DataDefinition(ilwis.NumericDomain("code=value"), ilwis.NumericRange(0.0, 500.0, 0.01))
rcNew = ilwis.RasterCoverage()
rcNew.setSize(ilwis.Size(size[1],size[0],12))
rcNew.setGeoReference(grf)
rcNew.setDataDef(dfNum)

In [ ]:
all_layers = []

for month in range(1,13):
    date_start = date(year, month, 1)
    date_start_fn = date_start.strftime('%Y%m%d')
    filename = 'data/precipitation_' + date_start_fn + '.tif'
    print('Reading:',filename)
    with rasterio.open(filename) as ds:
        data = ds.read(1)
        data = data * 24 * 31 #initial data in mm/hr
        all_layers.append(data)
all_layers = np.array(all_layers)

In [ ]:
rcNew.array2raster(all_layers)  

#rcNew.pix2value(ilwis.Pixel(4,0)) #just to show that data is there

In [ ]:
for month in range(12):
    print(rcNew.pix2value(ilwis.Pixel(100,101,month)))

In [ ]:
#rcNew.store('precipitation_2020.mpl')

In [ ]:
ilwis.operations()

In [ ]:
ilwis.operationMetaData('aggregaterasterstatistics')

In [ ]:
rcFlat = ilwis.do('aggregaterasterstatistics', rcNew, 'sum')

In [ ]:
print(rcFlat.size())

In [ ]:
rcFlat.store('pcpsum_2020.mpr')